In [2]:
import numpy as np
import pandas as pd
import matplotlib
import seaborn
import re
import statsmodels.formula.api

from sklearn.linear_model import SGDClassifier
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score

import gensim
from gensim.models import Word2Vec

In [3]:
# Configure how graphs will show up in this notebook
%matplotlib inline
seaborn.set_context('notebook', rc={'figure.figsize': (10, 6)}, font_scale=1.5)


### Define useful functions

In [4]:
def get_embedding_dataframe(model_asia_2500):
    '''Function to get the embedding dataframe from a word2vec model'''
    vocabulary = model_asia_2500.wv.vocab

    vectors = {}
    for word in vocabulary:
        vectors[word] = model_asia_2500[word]
        if len(vectors)%10000 == 0:
            print(len(vectors))
    print('Dataframe Done!')

    embedding_a2500 = pd.DataFrame.from_dict(vectors, orient='index')
    return embedding_a2500

In [5]:
def load_lexicon(filename):
    """
    Load a file from Bing Liu's sentiment lexicon
    (https://www.cs.uic.edu/~liub/FBS/sentiment-analysis.html), containing
    English words in Latin-1 encoding.
    
    One file contains a list of positive words, and the other contains
    a list of negative words. The files contain comment lines starting
    with ';' and blank lines, which should be skipped.
    """
    lexicon = []
    with open(filename, encoding='latin-1') as infile:
        for line in infile:
            line = line.rstrip()
            if line and not line.startswith(';'):
                lexicon.append(line)
    return lexicon

In [6]:
def check_in_vocab(pos_words, embedding_a2500):
    '''Function to keep positive or negative words that are in the vocabulary'''
    counter = 0
    checked_words = []
    for word in pos_words:
        if word not in list(embedding_a2500.index):
            print('{} not in list'.format(word))
        else:
            checked_words.append(word)
            print('{} checked words'.format(len(checked_words)))
    return checked_words

In [7]:
def get_sa_accuracy(pos_words, neg_words, embedding_a2500):
    '''Function to get the accuracy of a sentiment analysis log classifier trained with the passed embedding'''
    
    # Keep positive and negative words that are in the embedding
    print("Start with {} positive words, {} negative words".format(len(pos_words), len(neg_words)))
    pos_words = check_in_vocab(pos_words, embedding_a2500)
    neg_words = check_in_vocab(neg_words, embedding_a2500)
    print("After check: {} positive words, {} negative words".format(len(pos_words), len(neg_words)))
    
    # Get positive and negative vectors
    pos_vectors = embedding_a2500.loc[pos_words].dropna()
    neg_vectors = embedding_a2500.loc[neg_words].dropna()
    
    vectors = pd.concat([pos_vectors, neg_vectors])
    targets = np.array([1 for entry in pos_vectors.index] + [-1 for entry in neg_vectors.index])
    labels = list(pos_vectors.index) + list(neg_vectors.index)
    
    train_vectors, test_vectors, train_targets, test_targets, train_labels, test_labels = \
        train_test_split(vectors, targets, labels, test_size=0.1, random_state=0)
    
    sentiment_classifier = SGDClassifier(loss='log', random_state=0)
    sentiment_classifier.fit(train_vectors, train_targets)
    
    accuracy = accuracy_score(sentiment_classifier.predict(test_vectors), test_targets)
    return accuracy

### Get all embedding to be evaluated 

In [8]:
model_baseline = Word2Vec.load("../wikipedia_corpus/modelos_vectores/baseline/wiki_en.txt.model")

#model_asia_2500 = Word2Vec.load("../wikipedia_corpus/modelos_vectores/debiased_asian/wiki_cds_aw_2500.txt.model")
#model_black_2500 = Word2Vec.load("../wikipedia_corpus/modelos_vectores/debiased_black/wiki_cds_bw_2500.txt.model")
#model_hispanic_2500 = Word2Vec.load("../wikipedia_corpus/modelos_vectores/debiased_hispanic/wiki_cds_hw_2500.txt.model")

#model_asia = Word2Vec.load("../wikipedia_corpus/modelos_vectores/debiased_asian/cds/wiki_cds_aw.txt.model")
#model_black = Word2Vec.load("../wikipedia_corpus/modelos_vectores/debiased_black/cds/wiki_cds_bw.txt.model")
#model_hispanic = Word2Vec.load("../wikipedia_corpus/modelos_vectores/debiased_hispanic/cds/wiki_cds_hw.txt.model")

In [9]:
embedding_baseline = get_embedding_dataframe(model_baseline)

/Users/gabrielamaylagunes/Desktop/Berkeley/berkeley/lib/python3.7/site-packages/ipykernel_launcher.py:7: DeprecationWarning: Call to deprecated `__getitem__` (Method will be removed in 4.0.0, use self.wv.__getitem__() instead).
  import sys


10000
20000
30000
40000
50000
60000
70000
80000
90000
100000
110000
120000
130000
140000
150000
160000
170000
180000
190000
200000
210000
220000
230000
240000
250000
260000
270000
280000
290000
300000
310000
320000
330000
340000
350000
360000
370000
380000
390000
400000
410000
420000
430000
440000
450000
460000
470000
480000
490000
500000
510000
520000
530000
540000
550000
560000
570000
580000
590000
600000
610000
620000
630000
640000
650000
660000
670000
680000
690000
700000
710000
720000
730000
740000
750000
760000
770000
780000
790000
800000
810000
820000
830000
840000
850000
860000
870000
880000
890000
900000
910000
920000
930000
940000
950000
960000
970000
980000
990000
1000000
1010000
1020000
1030000
1040000
1050000
1060000
1070000
1080000
1090000
1100000
1110000
1120000
1130000
1140000
1150000
1160000
1170000
1180000
1190000
1200000
1210000
1220000
1230000
1240000
1250000
1260000
1270000
1280000
1290000
1300000
1310000
1320000
1330000
1340000
1350000
1360000
1370000
1380000
1390

In [10]:
#embedding_asia_2500 = get_embedding_dataframe(model_asia_2500)

In [11]:
#embedding_black_2500 = get_embedding_dataframe(model_black_2500)

In [12]:
#embedding_hispanic_2500 = get_embedding_dataframe(model_hispanic_2500)

In [13]:
#embedding_asia = get_embedding_dataframe(model_asia)

In [14]:
#embedding_black = get_embedding_dataframe(model_black)

In [15]:
#embedding_hispanic = get_embedding_dataframe(model_hispanic)

### Get positive and negative words

In [16]:
pos_words = load_lexicon('data/positive-words.txt')
neg_words = load_lexicon('data/negative-words.txt')

### Evaluate the embeddings

In [17]:
accuracy_base = get_sa_accuracy(pos_words, neg_words, embedding_baseline)

#accuracy_a25 = get_sa_accuracy(pos_words, neg_words, embedding_asia_2500)
#accuracy_b25 = get_sa_accuracy(pos_words, neg_words, embedding_black_2500)
#accuracy_h25 = get_sa_accuracy(pos_words, neg_words, embedding_hispanic_2500)

#accuracy_a = get_sa_accuracy(pos_words, neg_words, embedding_asia)
#accuracy_b = get_sa_accuracy(pos_words, neg_words, embedding_black)
#accuracy_h = get_sa_accuracy(pos_words, neg_words, embedding_hispanic)

Start with 2006 positive words, 4783 negative words
a+ not in list
1 checked words
2 checked words
3 checked words
4 checked words
accessable not in list
5 checked words
6 checked words
7 checked words
8 checked words
9 checked words
10 checked words
11 checked words
accomodative not in list
12 checked words
13 checked words
14 checked words
15 checked words
16 checked words
17 checked words
18 checked words
19 checked words
20 checked words
achievible not in list
21 checked words
22 checked words
23 checked words
24 checked words
25 checked words
26 checked words
27 checked words
28 checked words
29 checked words
30 checked words
31 checked words
32 checked words
33 checked words
34 checked words
35 checked words
36 checked words
37 checked words
38 checked words
39 checked words
40 checked words
41 checked words
42 checked words
43 checked words
44 checked words
45 checked words
46 checked words
47 checked words
48 checked words
49 checked words
50 checked words
51 checked words
52 c

423 checked words
424 checked words
425 checked words
426 checked words
427 checked words
428 checked words
429 checked words
dummy-proof not in list
430 checked words
431 checked words
432 checked words
433 checked words
434 checked words
435 checked words
436 checked words
437 checked words
438 checked words
439 checked words
440 checked words
441 checked words
442 checked words
443 checked words
444 checked words
445 checked words
easy-to-use not in list
446 checked words
447 checked words
448 checked words
449 checked words
ecenomical not in list
450 checked words
451 checked words
452 checked words
453 checked words
454 checked words
455 checked words
456 checked words
457 checked words
458 checked words
459 checked words
460 checked words
461 checked words
462 checked words
463 checked words
464 checked words
465 checked words
466 checked words
467 checked words
468 checked words
469 checked words
470 checked words
471 checked words
472 checked words
473 checked words
474 checked

836 checked words
837 checked words
838 checked words
839 checked words
840 checked words
841 checked words
842 checked words
843 checked words
844 checked words
845 checked words
846 checked words
847 checked words
848 checked words
heroize not in list
849 checked words
high-quality not in list
high-spirited not in list
850 checked words
851 checked words
852 checked words
853 checked words
854 checked words
855 checked words
856 checked words
857 checked words
858 checked words
859 checked words
860 checked words
861 checked words
862 checked words
863 checked words
864 checked words
865 checked words
866 checked words
867 checked words
868 checked words
869 checked words
870 checked words
871 checked words
872 checked words
873 checked words
874 checked words
875 checked words
876 checked words
877 checked words
878 checked words
879 checked words
880 checked words
881 checked words
882 checked words
883 checked words
884 checked words
885 checked words
886 checked words
887 checked

1239 checked words
1240 checked words
1241 checked words
1242 checked words
1243 checked words
1244 checked words
1245 checked words
1246 checked words
1247 checked words
1248 checked words
1249 checked words
1250 checked words
1251 checked words
1252 checked words
1253 checked words
1254 checked words
1255 checked words
1256 checked words
1257 checked words
1258 checked words
1259 checked words
1260 checked words
1261 checked words
problem-free not in list
problem-solver not in list
1262 checked words
1263 checked words
1264 checked words
1265 checked words
1266 checked words
1267 checked words
1268 checked words
1269 checked words
1270 checked words
1271 checked words
1272 checked words
1273 checked words
1274 checked words
1275 checked words
1276 checked words
1277 checked words
1278 checked words
1279 checked words
1280 checked words
1281 checked words
1282 checked words
1283 checked words
1284 checked words
1285 checked words
1286 checked words
1287 checked words
1288 checked word

1641 checked words
1642 checked words
1643 checked words
1644 checked words
1645 checked words
1646 checked words
1647 checked words
1648 checked words
swankier not in list
1649 checked words
1650 checked words
1651 checked words
1652 checked words
1653 checked words
1654 checked words
1655 checked words
1656 checked words
1657 checked words
1658 checked words
1659 checked words
1660 checked words
1661 checked words
1662 checked words
1663 checked words
1664 checked words
1665 checked words
1666 checked words
1667 checked words
1668 checked words
1669 checked words
1670 checked words
1671 checked words
1672 checked words
1673 checked words
1674 checked words
1675 checked words
1676 checked words
1677 checked words
1678 checked words
1679 checked words
1680 checked words
1681 checked words
1682 checked words
1683 checked words
1684 checked words
1685 checked words
1686 checked words
1687 checked words
1688 checked words
1689 checked words
thumb-up not in list
thumbs-up not in list
1690 

...

2587 checked words
2588 checked words
2589 checked words
2590 checked words
2591 checked words
2592 checked words
2593 checked words
2594 checked words
2595 checked words
2596 checked words
2597 checked words
2598 checked words
2599 checked words
2600 checked words
2601 checked words
2602 checked words
2603 checked words
2604 checked words
2605 checked words
2606 checked words
2607 checked words
2608 checked words
2609 checked words
2610 checked words
2611 checked words
2612 checked words
2613 checked words
2614 checked words
2615 checked words
2616 checked words
2617 checked words
2618 checked words
2619 checked words
2620 checked words
2621 checked words
2622 checked words
2623 checked words
2624 checked words
2625 checked words
2626 checked words
2627 checked words
2628 checked words
2629 checked words
2630 checked words
martyrdom-seeking not in list
2631 checked words
2632 checked words
2633 checked words
2634 checked words
2635 checked words
2636 checked words
2637 checked words
2

2987 checked words
2988 checked words
2989 checked words
2990 checked words
2991 checked words
2992 checked words
2993 checked words
2994 checked words
2995 checked words
2996 checked words
2997 checked words
2998 checked words
2999 checked words
3000 checked words
3001 checked words
3002 checked words
3003 checked words
3004 checked words
paralize not in list
3005 checked words
3006 checked words
3007 checked words
3008 checked words
3009 checked words
3010 checked words
3011 checked words
3012 checked words
3013 checked words
3014 checked words
3015 checked words
3016 checked words
3017 checked words
3018 checked words
3019 checked words
3020 checked words
3021 checked words
3022 checked words
3023 checked words
3024 checked words
3025 checked words
3026 checked words
3027 checked words
3028 checked words
3029 checked words
3030 checked words
3031 checked words
3032 checked words
3033 checked words
3034 checked words
perfidity not in list
3035 checked words
3036 checked words
3037 ch

run-down not in list
3402 checked words
3403 checked words
3404 checked words
3405 checked words
3406 checked words
3407 checked words
3408 checked words
3409 checked words
3410 checked words
3411 checked words
3412 checked words
3413 checked words
3414 checked words
3415 checked words
3416 checked words
3417 checked words
3418 checked words
3419 checked words
3420 checked words
3421 checked words
3422 checked words
3423 checked words
3424 checked words
3425 checked words
3426 checked words
3427 checked words
3428 checked words
3429 checked words
3430 checked words
3431 checked words
3432 checked words
3433 checked words
3434 checked words
3435 checked words
3436 checked words
3437 checked words
3438 checked words
3439 checked words
3440 checked words
3441 checked words
3442 checked words
3443 checked words
3444 checked words
3445 checked words
3446 checked words
3447 checked words
3448 checked words
scandels not in list
3449 checked words
3450 checked words
3451 checked words
3452 che

3787 checked words
3788 checked words
3789 checked words
3790 checked words
3791 checked words
3792 checked words
3793 checked words
3794 checked words
3795 checked words
3796 checked words
3797 checked words
3798 checked words
3799 checked words
3800 checked words
3801 checked words
3802 checked words
3803 checked words
3804 checked words
3805 checked words
3806 checked words
3807 checked words
3808 checked words
3809 checked words
3810 checked words
3811 checked words
3812 checked words
3813 checked words
3814 checked words
3815 checked words
3816 checked words
3817 checked words
3818 checked words
3819 checked words
3820 checked words
3821 checked words
3822 checked words
3823 checked words
3824 checked words
3825 checked words
3826 checked words
3827 checked words
3828 checked words
3829 checked words
3830 checked words
3831 checked words
3832 checked words
3833 checked words
3834 checked words
3835 checked words
3836 checked words
3837 checked words
3838 checked words
3839 checked

4188 checked words
4189 checked words
4190 checked words
4191 checked words
4192 checked words
4193 checked words
4194 checked words
4195 checked words
4196 checked words
4197 checked words
4198 checked words
4199 checked words
4200 checked words
4201 checked words
4202 checked words
4203 checked words
4204 checked words
4205 checked words
4206 checked words
4207 checked words
4208 checked words
4209 checked words
4210 checked words
4211 checked words
4212 checked words
unprove not in list
4213 checked words
4214 checked words
unproves not in list
unproving not in list
4215 checked words
4216 checked words
4217 checked words
4218 checked words
4219 checked words
4220 checked words
4221 checked words
4222 checked words
4223 checked words
4224 checked words
4225 checked words
4226 checked words
4227 checked words
4228 checked words
4229 checked words
4230 checked words
4231 checked words
4232 checked words
4233 checked words
4234 checked words
4235 checked words
4236 checked words
4237 c

In [18]:
print('Baseline accuracy: {}'.format(accuracy_base))
print('---------- First Round of Experiments ----------')
#print('Debiased asian accuracy: {}'.format(accuracy_a))
#print('Debiased black accuracy: {}'.format(accuracy_b))
#print('Debiased asian accuracy: {}'.format(accuracy_h))
#print('---------- 2500 Pairs Experiments ----------')
#print('Debiased asian accuracy: {}'.format(accuracy_a25))
#print('Debiased black accuracy: {}'.format(accuracy_b25))
#print('Debiased asian accuracy: {}'.format(accuracy_h25))

Baseline accuracy: 0.9131121642969984
---------- First Round of Experiments ----------


model_asia = Word2Vec.load("../wikipedia_corpus/modelos_vectores/debiased_asian/cds/wiki_cds_aw.txt.model")
embedding_asia = get_embedding_dataframe(model_asia)
accuracy_a = get_sa_accuracy(pos_words, neg_words, embedding_asia)
print('Debiased asian accuracy: {}'.format(accuracy_a))


In [98]:
def get_embedding_dataframe(model_asia_2500):
    '''Function to get the embedding dataframe from a word2vec model'''
    vocabulary = model_asia_2500.wv.vocab

    vectors = {}
    for word in vocabulary:
        vectors[word] = model_asia_2500[word]
        if len(vectors)%10000 == 0:
            print(len(vectors))

    embedding_a2500 = pd.DataFrame.from_dict(vectors, orient='index')

In [25]:
vectors 

{'anarchism': array([-6.7739546e-01,  1.9972286e+00, -1.1702502e+00,  7.8189856e-01,
        -1.5448499e+00,  2.1262805e-01, -1.0357157e-01, -2.2355352e-02,
        -6.9877487e-01, -2.4583054e-01,  2.2251309e-01,  5.3001654e-01,
         1.0038409e-01, -4.0294996e-01,  2.6867664e+00,  1.3441683e-01,
         1.2546266e+00,  2.2598357e+00, -7.2121805e-01,  2.0376551e+00,
         1.9808810e+00,  2.5466028e-01, -3.1447697e-01,  5.5362040e-01,
         4.6596152e-01, -1.8812193e+00,  1.4626861e+00,  7.9192859e-01,
        -3.2358521e-01,  2.3366330e+00,  1.4560571e+00,  2.1547248e+00,
        -2.5740767e-01,  1.9538024e-02, -5.4476190e-01, -7.9865974e-01,
        -6.2263691e-01,  4.9545094e-01, -1.0918137e+00, -7.8560650e-01,
        -1.4955013e-01, -2.0492625e+00, -3.1436652e-01,  6.2418830e-01,
         4.8325250e-01, -1.0411384e+00,  1.4036274e+00, -7.3518103e-01,
         5.2176297e-01, -1.7135856e+00,  1.0955441e+00,  8.0346465e-01,
         3.2451718e+00, -1.2662033e+00, -1.9391831e

In [26]:
embedding_a2500 = pd.DataFrame.from_dict(vectors, orient='index')

In [30]:
embedding_a2500

0         1         2         3         4         5    \
anarchism     -0.677395  1.997229 -1.170250  0.781899 -1.544850  0.212628   
is            -1.271925  0.317520  0.587524 -1.590939  1.805579  3.271520   
political     -0.575293  0.379511 -0.200807  2.794323  2.295680 -1.929802   
philosophy    -0.554174  0.796576 -0.481884  1.028678 -0.232604 -0.620387   
and            1.278285  0.700774  0.625927  0.114519 -0.568226 -1.186997   
...                 ...       ...       ...       ...       ...       ...   
rahamaniyya    0.081041 -0.025233 -0.065550 -0.060848 -0.054977  0.038926   
brownephilus   0.050691  0.064331 -0.006600  0.024677 -0.000470  0.053396   
arthrorhaphis -0.149217 -0.011536  0.009145  0.150467 -0.036334 -0.041734   
lozéron       -0.022423 -0.014166  0.014632  0.042963 -0.041447  0.009967   
šramek        -0.002309 -0.000699 -0.033541  0.034136  0.031264  0.072169   

                    6         7         8         9    ...       390  \
anarchism     -0.103572 -0.022355 -0.698775 -0.245831  ... -1.100299   
is            -1.558706 -0.744816 -3.502354 -1.805017  ...  0.969485   
political      0.659704 -0.370408  1.488716  0.666117  ... -1.954145   
philosophy     4.694561  0.194813  0.294529  1.028688  ...  0.057723   
and            0.373479  0.800536 -0.826780  0.752869  ... -0.531335   
...                 ...       ...       ...       ...  ...       ...   
rahamaniyya   -0.003999 -0.024422  0.018099  0.035540  ... -0.060329   
brownephilus   0.063106 -0.033856  0.045049  0.004887  ... -0.005044   
arthrorhaphis -0.017680  0.044998  0.026775 -0.004190  ... -0.037358   
lozéron        0.006557 -0.008901  0.033611 -0.026978  ... -0.017587   
šramek         0.008608 -0.029648 -0.000630  0.002919  ... -0.018510   

                    391       392       393       394       395       396  \
anarchism      0.338725 -2.204061  2.206183  0.335849  0.457160 -0.795412   
is            -1.901374 -1.776115  1.835072  2.714381 -1.588465 -0.628305   
political     -2.191603  1.387150  2.713866  0.772163  0.919588 -0.094075   
philosophy    -1.997118 -0.881024  1.539001 -0.077240  1.247500 -0.958384   
and            1.005999 -0.948884 -0.182035  0.148552 -0.493779 -0.756886   
...                 ...       ...       ...       ...       ...       ...   
rahamaniyya   -0.004388  0.018870 -0.047356  0.022545  0.060117 -0.001576   
brownephilus   0.035389 -0.001875 -0.002977  0.012079 -0.007881  0.002228   
arthrorhaphis -0.029628  0.002686 -0.037519  0.050038 -0.083686 -0.128999   
lozéron        0.002144 -0.050978 -0.033176 -0.044173 -0.006362  0.002263   
šramek         0.030081  0.016254  0.005748  0.000012  0.025529 -0.035063   

                    397       398       399  
anarchism     -1.607009  1.513756  1.562576  
is            -4.002725  0.626874  0.346741  
political     -1.273349  0.474619  0.187189  
philosophy    -1.156339  0.933986 -0.883267  
and           -0.887075  0.860371 -0.464958  
...                 ...       ...       ...  
rahamaniyya    0.034634 -0.016164 -0.099217  
brownephilus   0.044918 -0.025426 -0.047850  
arthrorhaphis  0.046655  0.033890  0.029157  
lozéron        0.053831 -0.006761 -0.002722  
šramek        -0.030022 -0.003888  0.009573  

[2499060 rows x 400 columns]

In [84]:
def load_lexicon(filename):
    """
    Load a file from Bing Liu's sentiment lexicon
    (https://www.cs.uic.edu/~liub/FBS/sentiment-analysis.html), containing
    English words in Latin-1 encoding.
    
    One file contains a list of positive words, and the other contains
    a list of negative words. The files contain comment lines starting
    with ';' and blank lines, which should be skipped.
    """
    lexicon = []
    with open(filename, encoding='latin-1') as infile:
        for line in infile:
            line = line.rstrip()
            if line and not line.startswith(';'):
                lexicon.append(line)
    return lexicon

pos_words = load_lexicon('data/positive-words.txt')
neg_words = load_lexicon('data/negative-words.txt')

In [41]:
len(pos_words)

2006

In [44]:
counter = 0
for word in pos_words:
    print(word)
    if word not in list(embedding_a2500.index):
        pos_words.remove(word)
        counter += 1
        print('{} words dropped: {}'.format(counter, word))

abound
abounds
abundance
abundant
accessible
acclaim
acclaimed
acclamation
accolade
accolades
accommodative
accomplish
accomplished
accomplishment
accomplishments
accurate
accurately
achievable
achievement
achievements
acumen
adaptable
adaptive
adequate
adjustable
admirable
admirably
admiration
admire
admirer
admiring
admiringly
adorable
adore
adored
adorer
adoring
adoringly
adroit
adroitly
adulate
adulation
adulatory
advanced
advantage
advantageous
advantageously
advantages
adventuresome
adventurous
advocate
advocated
advocates
affability
affable
affably
affectation
affection
affectionate
affinity
affirm
affirmation
affirmative
affluence
affluent
afford
affordable
affordably
agile
agilely
agility
agreeable
agreeableness
agreeably
alluring
alluringly
altruistic
altruistically
amaze
amazed
amazement
amazes
amazing
amazingly
ambitious
ambitiously
ameliorate
amenable
amenity
amiability
amiable
amicability
amicable
amicably
amity
ample
amply
amuse
amusing
amusingly
angel
angelic
apotheosis

gentlest
genuine
gifted
glad
gladden
gladly
gladness
glamorous
glee
gleeful
gleefully
glimmer
glimmering
glisten
glistening
glitter
glitz
glorify
glorious
gloriously
glory
glow
glowing
glowingly
god-given
35 words dropped: god-given
godlike
godsend
gold
golden
good
goodly
goodness
goodwill
goood
gooood
gorgeous
gorgeously
grace
graceful
gracefully
gracious
graciously
graciousness
grand
grandeur
grateful
gratefully
gratification
gratified
gratifies
gratify
gratifying
gratifyingly
gratitude
great
greatest
greatness
grin
groundbreaking
guarantee
guidance
guiltless
gumption
gush
gusto
gutsy
hail
halcyon
hale
hallmark
hallmarks
hallowed
handier
handily
hands-down
36 words dropped: hands-down
handsomely
handy
happier
happily
happiness
happy
hard-working
37 words dropped: hard-working
hardy
harmless
harmonious
harmoniously
harmonize
harmony
headway
heal
healthful
healthy
hearten
heartening
heartfelt
heartily
heartwarming
heaven
heavenly
helped
helpful
helping
hero
heroic
heroically
heroine
he

sensationally
sensations
sensible
sensibly
sensitive
serene
serenity
sexy
sharp
sharper
sharpest
shimmering
shimmeringly
75 words dropped: shimmeringly
shiny
significant
silent
simpler
simplest
simplified
simplifies
simplify
simplifying
sincere
sincerely
sincerity
skill
skilled
skillful
skillfully
slammin
sleek
slick
smart
smarter
smartest
smartly
smile
smiles
smiling
smilingly
smitten
smooth
smoother
smoothes
smoothest
smoothly
snappy
snazzy
sociable
soft
softer
solace
solicitous
solicitously
solid
solidarity
soothe
soothingly
sophisticated
soulful
soundly
soundness
spacious
sparkle
sparkling
spectacular
spectacularly
speedily
speedy
spellbind
spellbinding
spellbindingly
spellbound
spirited
spiritual
splendid
splendidly
splendor
spontaneous
sporty
spotless
sprightly
stability
stabilize
stable
stainless
standout
state-of-the-art
76 words dropped: state-of-the-art
statuesque
staunch
staunchly
staunchness
steadfast
steadfastly
steadfastness
steadiest
steadiness
steady
stellar
stellarly
7

In [53]:
len(pos_words)

1889

In [83]:
def check_in_vocab(pos_words, embedding_a2500):
    '''Function to keep positive or negative words that are in the vocabulary'''
    counter = 0
    checked_words = []
    for word in pos_words:
        if word not in list(embedding_a2500.index):
            print('{} not in list'.format(word))
        else:
            checked_words.append(word)
            print('{} checked words'.format(len(checked_words)))
    return checked_words

In [85]:
pos_words = check_in_vocab(pos_words, embedding_a2500)
neg_words = check_in_vocab(neg_words, embedding_a2500)

a+ not in list
1 checked words
2 checked words
3 checked words
4 checked words
accessable not in list
5 checked words
6 checked words
7 checked words
8 checked words
9 checked words
10 checked words
11 checked words
accomodative not in list
12 checked words
13 checked words
14 checked words
15 checked words
16 checked words
17 checked words
18 checked words
19 checked words
20 checked words
achievible not in list
21 checked words
22 checked words
23 checked words
24 checked words
25 checked words
26 checked words
27 checked words
28 checked words
29 checked words
30 checked words
31 checked words
32 checked words
33 checked words
34 checked words
35 checked words
36 checked words
37 checked words
38 checked words
39 checked words
40 checked words
41 checked words
42 checked words
43 checked words
44 checked words
45 checked words
46 checked words
47 checked words
48 checked words
49 checked words
50 checked words
51 checked words
52 checked words
53 checked words
54 checked words
55 ch

424 checked words
425 checked words
426 checked words
427 checked words
428 checked words
429 checked words
dummy-proof not in list
430 checked words
431 checked words
432 checked words
433 checked words
434 checked words
435 checked words
436 checked words
437 checked words
438 checked words
439 checked words
440 checked words
441 checked words
442 checked words
443 checked words
444 checked words
445 checked words
easy-to-use not in list
446 checked words
447 checked words
448 checked words
449 checked words
ecenomical not in list
450 checked words
451 checked words
452 checked words
453 checked words
454 checked words
455 checked words
456 checked words
457 checked words
458 checked words
459 checked words
460 checked words
461 checked words
462 checked words
463 checked words
464 checked words
465 checked words
466 checked words
467 checked words
468 checked words
469 checked words
470 checked words
471 checked words
472 checked words
473 checked words
474 checked words
475 checked

839 checked words
840 checked words
841 checked words
842 checked words
843 checked words
844 checked words
845 checked words
846 checked words
847 checked words
848 checked words
heroize not in list
849 checked words
high-quality not in list
high-spirited not in list
850 checked words
851 checked words
852 checked words
853 checked words
854 checked words
855 checked words
856 checked words
857 checked words
858 checked words
859 checked words
860 checked words
861 checked words
862 checked words
863 checked words
864 checked words
865 checked words
866 checked words
867 checked words
868 checked words
869 checked words
870 checked words
871 checked words
872 checked words
873 checked words
874 checked words
875 checked words
876 checked words
877 checked words
878 checked words
879 checked words
880 checked words
881 checked words
882 checked words
883 checked words
884 checked words
885 checked words
886 checked words
887 checked words
imaculate not in list
888 checked words
889 che

1243 checked words
1244 checked words
1245 checked words
1246 checked words
1247 checked words
1248 checked words
1249 checked words
1250 checked words
1251 checked words
1252 checked words
1253 checked words
1254 checked words
1255 checked words
1256 checked words
1257 checked words
1258 checked words
1259 checked words
1260 checked words
1261 checked words
problem-free not in list
problem-solver not in list
1262 checked words
1263 checked words
1264 checked words
1265 checked words
1266 checked words
1267 checked words
1268 checked words
1269 checked words
1270 checked words
1271 checked words
1272 checked words
1273 checked words
1274 checked words
1275 checked words
1276 checked words
1277 checked words
1278 checked words
1279 checked words
1280 checked words
1281 checked words
1282 checked words
1283 checked words
1284 checked words
1285 checked words
1286 checked words
1287 checked words
1288 checked words
1289 checked words
1290 checked words
1291 checked words
1292 checked word

1644 checked words
1645 checked words
1646 checked words
1647 checked words
1648 checked words
swankier not in list
1649 checked words
1650 checked words
1651 checked words
1652 checked words
1653 checked words
1654 checked words
1655 checked words
1656 checked words
1657 checked words
1658 checked words
1659 checked words
1660 checked words
1661 checked words
1662 checked words
1663 checked words
1664 checked words
1665 checked words
1666 checked words
1667 checked words
1668 checked words
1669 checked words
1670 checked words
1671 checked words
1672 checked words
1673 checked words
1674 checked words
1675 checked words
1676 checked words
1677 checked words
1678 checked words
1679 checked words
1680 checked words
1681 checked words
1682 checked words
1683 checked words
1684 checked words
1685 checked words
1686 checked words
1687 checked words
1688 checked words
1689 checked words
thumb-up not in list
thumbs-up not in list
1690 checked words
1691 checked words
time-honored not in list

...

2589 checked words
2590 checked words
2591 checked words
2592 checked words
2593 checked words
2594 checked words
2595 checked words
2596 checked words
2597 checked words
2598 checked words
2599 checked words
2600 checked words
2601 checked words
2602 checked words
2603 checked words
2604 checked words
2605 checked words
2606 checked words
2607 checked words
2608 checked words
2609 checked words
2610 checked words
2611 checked words
2612 checked words
2613 checked words
2614 checked words
2615 checked words
2616 checked words
2617 checked words
2618 checked words
2619 checked words
2620 checked words
2621 checked words
2622 checked words
2623 checked words
2624 checked words
2625 checked words
2626 checked words
2627 checked words
2628 checked words
2629 checked words
2630 checked words
martyrdom-seeking not in list
2631 checked words
2632 checked words
2633 checked words
2634 checked words
2635 checked words
2636 checked words
2637 checked words
2638 checked words
2639 checked words
2

2989 checked words
2990 checked words
2991 checked words
2992 checked words
2993 checked words
2994 checked words
2995 checked words
2996 checked words
2997 checked words
2998 checked words
2999 checked words
3000 checked words
3001 checked words
3002 checked words
3003 checked words
3004 checked words
paralize not in list
3005 checked words
3006 checked words
3007 checked words
3008 checked words
3009 checked words
3010 checked words
3011 checked words
3012 checked words
3013 checked words
3014 checked words
3015 checked words
3016 checked words
3017 checked words
3018 checked words
3019 checked words
3020 checked words
3021 checked words
3022 checked words
3023 checked words
3024 checked words
3025 checked words
3026 checked words
3027 checked words
3028 checked words
3029 checked words
3030 checked words
3031 checked words
3032 checked words
3033 checked words
3034 checked words
perfidity not in list
3035 checked words
3036 checked words
3037 checked words
3038 checked words
3039 ch

3403 checked words
3404 checked words
3405 checked words
3406 checked words
3407 checked words
3408 checked words
3409 checked words
3410 checked words
3411 checked words
3412 checked words
3413 checked words
3414 checked words
3415 checked words
3416 checked words
3417 checked words
3418 checked words
3419 checked words
3420 checked words
3421 checked words
3422 checked words
3423 checked words
3424 checked words
3425 checked words
3426 checked words
3427 checked words
3428 checked words
3429 checked words
3430 checked words
3431 checked words
3432 checked words
3433 checked words
3434 checked words
3435 checked words
3436 checked words
3437 checked words
3438 checked words
3439 checked words
3440 checked words
3441 checked words
3442 checked words
3443 checked words
3444 checked words
3445 checked words
3446 checked words
3447 checked words
3448 checked words
scandels not in list
3449 checked words
3450 checked words
3451 checked words
3452 checked words
3453 checked words
3454 check

3789 checked words
3790 checked words
3791 checked words
3792 checked words
3793 checked words
3794 checked words
3795 checked words
3796 checked words
3797 checked words
3798 checked words
3799 checked words
3800 checked words
3801 checked words
3802 checked words
3803 checked words
3804 checked words
3805 checked words
3806 checked words
3807 checked words
3808 checked words
3809 checked words
3810 checked words
3811 checked words
3812 checked words
3813 checked words
3814 checked words
3815 checked words
3816 checked words
3817 checked words
3818 checked words
3819 checked words
3820 checked words
3821 checked words
3822 checked words
3823 checked words
3824 checked words
3825 checked words
3826 checked words
3827 checked words
3828 checked words
3829 checked words
3830 checked words
3831 checked words
3832 checked words
3833 checked words
3834 checked words
3835 checked words
3836 checked words
3837 checked words
3838 checked words
3839 checked words
3840 checked words
3841 checked

4191 checked words
4192 checked words
4193 checked words
4194 checked words
4195 checked words
4196 checked words
4197 checked words
4198 checked words
4199 checked words
4200 checked words
4201 checked words
4202 checked words
4203 checked words
4204 checked words
4205 checked words
4206 checked words
4207 checked words
4208 checked words
4209 checked words
4210 checked words
4211 checked words
4212 checked words
unprove not in list
4213 checked words
4214 checked words
unproves not in list
unproving not in list
4215 checked words
4216 checked words
4217 checked words
4218 checked words
4219 checked words
4220 checked words
4221 checked words
4222 checked words
4223 checked words
4224 checked words
4225 checked words
4226 checked words
4227 checked words
4228 checked words
4229 checked words
4230 checked words
4231 checked words
4232 checked words
4233 checked words
4234 checked words
4235 checked words
4236 checked words
4237 checked words
4238 checked words
4239 checked words
4240 c

In [86]:
len(pos_words)

1853

In [87]:
len(neg_words)

4470

In [88]:
embedding_a2500.loc[pos_words]#embedding_a2500[[pos_words]]

0         1         2         3         4         5    \
abound     -0.980759 -0.591084 -0.400339 -0.489755 -1.303439  2.343123   
abounds    -1.332831 -0.218190  0.292943  1.296579 -1.004251  0.967017   
abundance   0.319666  0.697254  0.489060  1.797446 -1.686837  0.244877   
abundant   -1.470471  0.437138  1.271936  0.818472 -0.782104  1.967037   
accessible -0.920447 -1.950632  2.178997  0.663813 -1.535280  0.414359   
...              ...       ...       ...       ...       ...       ...   
youthful    0.536877 -1.298241 -0.257383 -0.748763 -0.389563  2.154991   
zeal        0.195192  0.072812  2.041131  0.722485 -1.359556  1.830388   
zenith     -0.413737 -0.026792 -0.785347 -0.690961  1.034168 -1.041736   
zest        1.526279 -0.608982  0.454587  0.968451 -2.120856  1.088241   
zippy      -0.076777 -1.889637 -0.581803 -0.644697 -1.630150 -0.933333   

                 6         7         8         9    ...       390       391  \
abound      0.770440  0.958940 -1.711670 -0.558688  ... -1.422382  1.664666   
abounds     0.162878 -0.038995 -0.815411 -1.671313  ... -1.616300  0.052504   
abundance  -1.131834 -0.214234 -0.869732 -0.963762  ... -2.751383  0.795672   
abundant   -0.775081  0.481779 -0.582014 -1.278570  ... -0.927335  1.501806   
accessible -2.249985  1.088146  1.659052 -0.511024  ... -0.219667  3.010701   
...              ...       ...       ...       ...  ...       ...       ...   
youthful   -1.922364  0.656056 -1.762276  0.425526  ... -2.046329 -0.769710   
zeal       -0.283723 -0.799660 -1.490877  0.151068  ...  0.658192 -2.507202   
zenith      0.311808  0.716992 -1.650189 -0.728443  ...  1.598029  1.022519   
zest       -1.002259 -1.245366 -1.839993  1.944920  ... -0.863220 -0.990673   
zippy      -1.213209 -0.543509  0.110506 -1.178785  ...  0.307554 -1.629155   

                 392       393       394       395       396       397  \
abound     -0.791393  0.347083  1.117443 -1.542373 -2.149451  0.191195   
abounds    -0.653078 -0.139632  0.890588 -0.413377 -0.887067  0.185895   
abundance  -2.125369  2.623740  1.998096 -2.202160 -1.086686 -0.418036   
abundant   -2.672320  3.522954  1.611128 -0.211548 -0.272429  2.605965   
accessible -0.281737  2.818406  1.583882  3.919586  0.387095 -0.564246   
...              ...       ...       ...       ...       ...       ...   
youthful   -0.383391  0.534112 -0.419157 -0.674501 -0.329586 -0.332668   
zeal       -1.220446 -1.382709  0.700697 -1.395324 -1.649958 -1.811446   
zenith      1.228913 -1.111414  0.443513  0.846795  0.758599 -1.673029   
zest        0.807426  0.745428  0.570056 -0.835089 -0.910279 -0.277710   
zippy      -0.564269  0.584190 -0.784695 -0.867110  0.225824  0.206924   

                 398       399  
abound     -0.696087 -0.051883  
abounds    -0.168839  0.735338  
abundance   1.406620  0.177419  
abundant    0.883888  1.030249  
accessible  3.632632  1.528832  
...              ...       ...  
youthful   -0.072834  2.131008  
zeal       -0.213330  1.878629  
zenith      0.365120  0.674833  
zest        0.798537  0.382707  
zippy      -0.780234  0.046515  

[1853 rows x 400 columns]

In [89]:
pos_vectors = embedding_a2500.loc[pos_words].dropna()
neg_vectors = embedding_a2500.loc[neg_words].dropna()

In [90]:
vectors = pd.concat([pos_vectors, neg_vectors])
targets = np.array([1 for entry in pos_vectors.index] + [-1 for entry in neg_vectors.index])
labels = list(pos_vectors.index) + list(neg_vectors.index)

In [91]:
train_vectors, test_vectors, train_targets, test_targets, train_labels, test_labels = \
    train_test_split(vectors, targets, labels, test_size=0.1, random_state=0)

In [93]:
sentiment_classifier = SGDClassifier(loss='log', random_state=0)
sentiment_classifier.fit(train_vectors, train_targets)

SGDClassifier(loss='log', random_state=0)

In [94]:
accuracy_score(sentiment_classifier.predict(test_vectors), test_targets)

0.9225908372827805

In [103]:
accuracy = get_sa_accuracy(pos_words, neg_words, embedding_a2500)

Start with 1853 positive words, 4470 negative words
1 checked words
2 checked words
3 checked words
4 checked words
5 checked words
6 checked words
7 checked words
8 checked words
9 checked words
10 checked words
11 checked words
12 checked words
13 checked words
14 checked words
15 checked words
16 checked words
17 checked words
18 checked words
19 checked words
20 checked words
21 checked words
22 checked words
23 checked words
24 checked words
25 checked words
26 checked words
27 checked words
28 checked words
29 checked words
30 checked words
31 checked words
32 checked words
33 checked words
34 checked words
35 checked words
36 checked words
37 checked words
38 checked words
39 checked words
40 checked words
41 checked words
42 checked words
43 checked words
44 checked words
45 checked words
46 checked words
47 checked words
48 checked words
49 checked words
50 checked words
51 checked words
52 checked words
53 checked words
54 checked words
55 checked words
56 checked words
57 ch

461 checked words
462 checked words
463 checked words
464 checked words
465 checked words
466 checked words
467 checked words
468 checked words
469 checked words
470 checked words
471 checked words
472 checked words
473 checked words
474 checked words
475 checked words
476 checked words
477 checked words
478 checked words
479 checked words
480 checked words
481 checked words
482 checked words
483 checked words
484 checked words
485 checked words
486 checked words
487 checked words
488 checked words
489 checked words
490 checked words
491 checked words
492 checked words
493 checked words
494 checked words
495 checked words
496 checked words
497 checked words
498 checked words
499 checked words
500 checked words
501 checked words
502 checked words
503 checked words
504 checked words
505 checked words
506 checked words
507 checked words
508 checked words
509 checked words
510 checked words
511 checked words
512 checked words
513 checked words
514 checked words
515 checked words
516 checke

918 checked words
919 checked words
920 checked words
921 checked words
922 checked words
923 checked words
924 checked words
925 checked words
926 checked words
927 checked words
928 checked words
929 checked words
930 checked words
931 checked words
932 checked words
933 checked words
934 checked words
935 checked words
936 checked words
937 checked words
938 checked words
939 checked words
940 checked words
941 checked words
942 checked words
943 checked words
944 checked words
945 checked words
946 checked words
947 checked words
948 checked words
949 checked words
950 checked words
951 checked words
952 checked words
953 checked words
954 checked words
955 checked words
956 checked words
957 checked words
958 checked words
959 checked words
960 checked words
961 checked words
962 checked words
963 checked words
964 checked words
965 checked words
966 checked words
967 checked words
968 checked words
969 checked words
970 checked words
971 checked words
972 checked words
973 checke

1355 checked words
1356 checked words
1357 checked words
1358 checked words
1359 checked words
1360 checked words
1361 checked words
1362 checked words
1363 checked words
1364 checked words
1365 checked words
1366 checked words
1367 checked words
1368 checked words
1369 checked words
1370 checked words
1371 checked words
1372 checked words
1373 checked words
1374 checked words
1375 checked words
1376 checked words
1377 checked words
1378 checked words
1379 checked words
1380 checked words
1381 checked words
1382 checked words
1383 checked words
1384 checked words
1385 checked words
1386 checked words
1387 checked words
1388 checked words
1389 checked words
1390 checked words
1391 checked words
1392 checked words
1393 checked words
1394 checked words
1395 checked words
1396 checked words
1397 checked words
1398 checked words
1399 checked words
1400 checked words
1401 checked words
1402 checked words
1403 checked words
1404 checked words
1405 checked words
1406 checked words
1407 checked

1789 checked words
1790 checked words
1791 checked words
1792 checked words
1793 checked words
1794 checked words
1795 checked words
1796 checked words
1797 checked words
1798 checked words
1799 checked words
1800 checked words
1801 checked words
1802 checked words
1803 checked words
1804 checked words
1805 checked words
1806 checked words
1807 checked words
1808 checked words
1809 checked words
1810 checked words
1811 checked words
1812 checked words
1813 checked words
1814 checked words
1815 checked words
1816 checked words
1817 checked words
1818 checked words
1819 checked words
1820 checked words
1821 checked words
1822 checked words
1823 checked words
1824 checked words
1825 checked words
1826 checked words
1827 checked words
1828 checked words
1829 checked words
1830 checked words
1831 checked words
1832 checked words
1833 checked words
1834 checked words
1835 checked words
1836 checked words
1837 checked words
1838 checked words
1839 checked words
1840 checked words
1841 checked

...

2589 checked words
2590 checked words
2591 checked words
2592 checked words
2593 checked words
2594 checked words
2595 checked words
2596 checked words
2597 checked words
2598 checked words
2599 checked words
2600 checked words
2601 checked words
2602 checked words
2603 checked words
2604 checked words
2605 checked words
2606 checked words
2607 checked words
2608 checked words
2609 checked words
2610 checked words
2611 checked words
2612 checked words
2613 checked words
2614 checked words
2615 checked words
2616 checked words
2617 checked words
2618 checked words
2619 checked words
2620 checked words
2621 checked words
2622 checked words
2623 checked words
2624 checked words
2625 checked words
2626 checked words
2627 checked words
2628 checked words
2629 checked words
2630 checked words
2631 checked words
2632 checked words
2633 checked words
2634 checked words
2635 checked words
2636 checked words
2637 checked words
2638 checked words
2639 checked words
2640 checked words
2641 checked

3022 checked words
3023 checked words
3024 checked words
3025 checked words
3026 checked words
3027 checked words
3028 checked words
3029 checked words
3030 checked words
3031 checked words
3032 checked words
3033 checked words
3034 checked words
3035 checked words
3036 checked words
3037 checked words
3038 checked words
3039 checked words
3040 checked words
3041 checked words
3042 checked words
3043 checked words
3044 checked words
3045 checked words
3046 checked words
3047 checked words
3048 checked words
3049 checked words
3050 checked words
3051 checked words
3052 checked words
3053 checked words
3054 checked words
3055 checked words
3056 checked words
3057 checked words
3058 checked words
3059 checked words
3060 checked words
3061 checked words
3062 checked words
3063 checked words
3064 checked words
3065 checked words
3066 checked words
3067 checked words
3068 checked words
3069 checked words
3070 checked words
3071 checked words
3072 checked words
3073 checked words
3074 checked

3456 checked words
3457 checked words
3458 checked words
3459 checked words
3460 checked words
3461 checked words
3462 checked words
3463 checked words
3464 checked words
3465 checked words
3466 checked words
3467 checked words
3468 checked words
3469 checked words
3470 checked words
3471 checked words
3472 checked words
3473 checked words
3474 checked words
3475 checked words
3476 checked words
3477 checked words
3478 checked words
3479 checked words
3480 checked words
3481 checked words
3482 checked words
3483 checked words
3484 checked words
3485 checked words
3486 checked words
3487 checked words
3488 checked words
3489 checked words
3490 checked words
3491 checked words
3492 checked words
3493 checked words
3494 checked words
3495 checked words
3496 checked words
3497 checked words
3498 checked words
3499 checked words
3500 checked words
3501 checked words
3502 checked words
3503 checked words
3504 checked words
3505 checked words
3506 checked words
3507 checked words
3508 checked

3889 checked words
3890 checked words
3891 checked words
3892 checked words
3893 checked words
3894 checked words
3895 checked words
3896 checked words
3897 checked words
3898 checked words
3899 checked words
3900 checked words
3901 checked words
3902 checked words
3903 checked words
3904 checked words
3905 checked words
3906 checked words
3907 checked words
3908 checked words
3909 checked words
3910 checked words
3911 checked words
3912 checked words
3913 checked words
3914 checked words
3915 checked words
3916 checked words
3917 checked words
3918 checked words
3919 checked words
3920 checked words
3921 checked words
3922 checked words
3923 checked words
3924 checked words
3925 checked words
3926 checked words
3927 checked words
3928 checked words
3929 checked words
3930 checked words
3931 checked words
3932 checked words
3933 checked words
3934 checked words
3935 checked words
3936 checked words
3937 checked words
3938 checked words
3939 checked words
3940 checked words
3941 checked

4321 checked words
4322 checked words
4323 checked words
4324 checked words
4325 checked words
4326 checked words
4327 checked words
4328 checked words
4329 checked words
4330 checked words
4331 checked words
4332 checked words
4333 checked words
4334 checked words
4335 checked words
4336 checked words
4337 checked words
4338 checked words
4339 checked words
4340 checked words
4341 checked words
4342 checked words
4343 checked words
4344 checked words
4345 checked words
4346 checked words
4347 checked words
4348 checked words
4349 checked words
4350 checked words
4351 checked words
4352 checked words
4353 checked words
4354 checked words
4355 checked words
4356 checked words
4357 checked words
4358 checked words
4359 checked words
4360 checked words
4361 checked words
4362 checked words
4363 checked words
4364 checked words
4365 checked words
4366 checked words
4367 checked words
4368 checked words
4369 checked words
4370 checked words
4371 checked words
4372 checked words
4373 checked

In [106]:
accuracy

0.9225908372827805